In [6]:
pip install rdkit

^C
Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


In [7]:
pip install chainer-chemistry

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
import logging
from rdkit import RDLogger
from chainer_chemistry import datasets

lg = RDLogger.logger()
lg.setLevel(RDLogger.CRITICAL)

logging.basicConfig(level=logging.INFO)

In [3]:
dataset_filepath = datasets.get_qm9_filepath()

print('dataset_filepath =', dataset_filepath)

dataset_filepath = C:\Users\riakh\.chainer\dataset\pfnet/chainer/qm9\qm9.csv


In [4]:
from chainer_chemistry.dataset.preprocessors.ggnn_preprocessor import \
    GGNNPreprocessor
    
preprocessor = GGNNPreprocessor()
dataset, dataset_smiles = datasets.get_qm9(preprocessor, labels=None, return_smiles=True)

100%|██████████| 133885/133885 [00:22<00:00, 5821.86it/s]
INFO:chainer_chemistry.dataset.parsers.data_frame_parser:Preprocess finished. FAIL 0, SUCCESS 133885, TOTAL 133885


In [5]:
print('dataset information...')
print('dataset', type(dataset), len(dataset))

print('smiles information...')
print('dataset_smiles', type(dataset_smiles), len(dataset_smiles))

dataset information...
dataset <class 'chainer_chemistry.datasets.numpy_tuple_dataset.NumpyTupleDataset'> 133885
smiles information...
dataset_smiles <class 'numpy.ndarray'> 133885


In [6]:
print('length of dataset:', len(dataset))

length of dataset: 133885


In [ ]:
# Print first 5 SMILES strings
for i in range(5):
    print(f"SMILES {i+1}: {dataset_smiles[i]}")


In [ ]:
from rdkit import Chem


for smile in dataset_smiles:
    mol = Chem.MolFromSmiles(smile)
    if mol is not None:  
        print(Chem.MolToInchiKey(mol))  


In [ ]:
print("Total number of SMILES:", len(dataset_smiles))
print("Type of dataset_smiles:", type(dataset_smiles))


In [ ]:
from IPython.display import display

molecules = [Chem.MolFromSmiles(smile) for smile in dataset_smiles[:5] if smile]
img = Draw.MolsToGridImage(molecules, molsPerRow=5, useSVG=True)  
display(img)


In [7]:
pip install torch-geometric

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


In [ ]:
# Assuming 'dataset_smiles' is a list of SMILES strings
print("First few SMILES entries:")
for i, smiles in enumerate(dataset_smiles[:5]): 
    print(f"{i + 1}: {smiles}")


In [ ]:

print("First few entries of the dataset:")
for i in range(min(5, len(dataset))):  
    print(f"Entry {i}: {dataset[i]}")


In [26]:
import numpy as np
import torch
from torch_geometric.data import Data
from rdkit import Chem
import pennylane as qml
import matplotlib.pyplot as plt

def smiles_to_graph_and_targets(smiles_list, dataset):
    data_list = []
    targets = []
    for smiles, data in zip(smiles_list, dataset):
        properties = data if len(data) > 0 else None
        mol = Chem.MolFromSmiles(smiles)
        if mol is None:
            continue

        atomic_nums = [atom.GetAtomicNum() for atom in mol.GetAtoms()]
        aromatics = [atom.GetIsAromatic() for atom in mol.GetAtoms()]
        hybridizations = [int(atom.GetHybridization()) for atom in mol.GetAtoms()]
        num_hydrogens = [atom.GetTotalNumHs() for atom in mol.GetAtoms()]

        x = np.column_stack([atomic_nums, aromatics, hybridizations, num_hydrogens])
        edge_index = []
        edge_attr = []
        bond_info = []

        for bond in mol.GetBonds():
            start, end = bond.GetBeginAtomIdx(), bond.GetEndAtomIdx()
            bond_type = bond.GetBondType()
            bond_label = {Chem.rdchem.BondType.SINGLE: 'single',
                          Chem.rdchem.BondType.DOUBLE: 'double',
                          Chem.rdchem.BondType.TRIPLE: 'triple',
                          Chem.rdchem.BondType.AROMATIC: 'aromatic'}.get(bond_type, 'single')
            bond_info.append((start, end, bond_label))
            edge_attr.append([1 if bond_label == bl else 0 for bl in ['single', 'double', 'triple', 'aromatic']])
            edge_index.append([start, end])
            # edge_index.append([end, start])

        edge_index = torch.tensor(edge_index, dtype=torch.long).t()
        edge_attr = torch.tensor(edge_attr, dtype=torch.float)
        x = torch.tensor(x, dtype=torch.float)
        data = Data(x=x, edge_index=edge_index, edge_attr=edge_attr, bond_info=bond_info)
        data_list.append(data)

        if properties is not None:
            target_value = properties[2][6]  # the target is in the 7th column of the third block
            targets.append(target_value)

    targets = torch.tensor(targets, dtype=torch.float)
    return data_list, targets

def split_data(graph_data, targets, train_size, val_size):
    print(f"Total graphs: {len(graph_data)}, Total targets: {len(targets)}")
    indices = np.random.permutation(len(graph_data))
    train_indices = indices[:train_size]
    val_indices = indices[train_size:train_size + val_size]

    train_data = [graph_data[i] for i in train_indices]
    train_targets = targets[train_indices]
    val_data = [graph_data[i] for i in val_indices]
    val_targets = targets[val_indices]

    return (train_data, train_targets), (val_data, val_targets)

def filter_graphs_by_num_atoms(graph_data, targets, num_atoms=6):
    filtered_graphs = [graph for graph in graph_data if graph.num_nodes == num_atoms]
    filtered_targets = [targets[i] for i, graph in enumerate(graph_data) if graph.num_nodes == num_atoms]
    return filtered_graphs, torch.tensor(filtered_targets, dtype=torch.float)

def batch_processing(graph_data, targets, batch_size):
    num_batches = len(graph_data) // batch_size
    for i in range(num_batches):
        batch_data = graph_data[i * batch_size: (i + 1) * batch_size]
        batch_targets = targets[i * batch_size: (i + 1) * batch_size]
        yield batch_data, batch_targets

def quantum_encode(features, use_atomic_num=True, use_nh=False, use_aromaticity=True, use_hybridization=True):
    encoded_params = []
    for feature in features:
        z, nh, aromatic, hybridization = feature.tolist()
        ry_angle, rz_angle = 0, 0

        if use_atomic_num and not use_nh and use_aromaticity and use_hybridization:
            ry_angle = (2 * z - 7) * np.pi / 4 if z is not None else 0
            rz_angle = (-1)**(2 * hybridization - 1) * np.pi / 6 if hybridization is not None else 0
        elif use_atomic_num and use_nh:
            ry_angle = (2 * z - 7) * np.pi / 4 if z is not None else 0
            rz_angle = 2 * np.pi * nh / 5 if nh is not None else 0
        elif use_atomic_num:
            if z in [5, 6, 7]:
                ry_angle = np.cos(-1 / 3)
            if z == 6:
                rz_angle = 2 * np.pi / 3
            elif z == 7:
                rz_angle = -2 * np.pi / 3

        encoded_params.append([ry_angle, rz_angle])
    return np.array(encoded_params)

def default_EDU(bond_params, rzz_param, wires):
    if len(wires) < 2:
        raise ValueError(f"Expected 'wires' to contain at least 2 elements, but got {len(wires)} elements: {wires}")
    
    print(f"Applying EDU on wires: {wires}")
    
    qml.RZ(bond_params[0], wires=wires[0])
    qml.RX(bond_params[1], wires=wires[0])
    qml.RZ(bond_params[0],wires=wires[1])
    qml.RX(bond_params[1], wires=wires[1])
    qml.CNOT(wires=wires)
    qml.RZ(rzz_param, wires=wires[1])
    qml.CNOT(wires=wires)
    qml.RX(bond_params[0], wires=wires[0])
    qml.RZ(bond_params[1], wires=wires[0])
    qml.RX(bond_params[0], wires=wires[1])
    qml.RZ(bond_params[1], wires=wires[1])

def quantum_circuit(graph, layer_params):
    num_layers = 3  # Fixed number of layers
    num_atoms = graph.num_nodes
    dev = qml.device('default.qubit', wires=num_atoms)

    @qml.qnode(dev, interface='torch')
    def circuit():
        encoded_features = quantum_encode(graph.x)
        for i in range(num_atoms):
            qml.RY(encoded_features[i][0], wires=i)
            qml.RZ(encoded_features[i][1], wires=i)

        for layer in range(num_layers): 
            rzz_param = layer_params['rzz_params'][layer]
            for i in range(num_atoms):
                qml.U3(layer_params['theta'][layer], layer_params['phi'][layer], layer_params['omega'][layer], wires=i)
            bond_order = ['single', 'aromatic', 'double', 'triple']
            sorted_bonds = sorted(graph.bond_info, key=lambda x: bond_order.index(x[2]))
            for start, end, bond_type in sorted_bonds:
                bond_edu_params = layer_params['edu'][bond_type]
                default_EDU(bond_edu_params, rzz_param, [start, end])
        return [qml.expval(qml.PauliZ(i)) for i in range(num_atoms)]
    
    qml_results = circuit()
    qml_results = torch.stack(qml_results).float()
    return qml_results

def train_and_plot(train_data, train_targets, val_data, val_targets, batch_size=30):
    layers = 3
    num_atoms = 6

    params = {
        'theta': [torch.tensor(np.random.random(), dtype=torch.float32, requires_grad=True) for _ in range(layers)],
        'phi': [torch.tensor(np.random.random(), dtype=torch.float32, requires_grad=True) for _ in range(layers)],
        'omega': [torch.tensor(np.random.random(), dtype=torch.float32, requires_grad=True) for _ in range(layers)],
        'rzz_params': [torch.tensor(np.random.random(), dtype=torch.float32, requires_grad=True) for _ in range(layers)],
        'edu': {
            'single': torch.tensor(np.random.random(2), dtype=torch.float32, requires_grad=True),
            'aromatic': torch.tensor(np.random.random(2), dtype=torch.float32, requires_grad=True),
            'double': torch.tensor(np.random.random(2), dtype=torch.float32, requires_grad=True),
            'triple': torch.tensor(np.random.random(2), dtype=torch.float32, requires_grad=True)
        }
    }

    all_params = []
    for key, value in params.items():
        if isinstance(value, list):
            all_params.extend(value)
        elif isinstance(value, dict):
            for subvalue in value.values():
                all_params.append(subvalue)
        else:
            all_params.append(value)  

    r0 = torch.tensor(0.1, dtype=torch.float32, requires_grad=True)
    r1 = torch.tensor(0.2, dtype=torch.float32, requires_grad=True)
    all_params += [r0, r1]

    optimizer = torch.optim.Adam(all_params, lr=0.01, betas=(0.9, 0.999))
    loss_func = torch.nn.MSELoss()
    train_losses = []
    val_losses = []

    for epoch in range(150):
        total_train_loss = 0
        train_batches = list(batch_processing(train_data, train_targets, batch_size))
        #val_batches = list(batch_processing(val_data, val_targets, batch_size))
        
        for batch_data, batch_targets in train_batches:
            optimizer.zero_grad()
            batch_loss = 0
            for data, target in zip(batch_data, batch_targets):
                print("Input shape:", data.x.shape)
                readout = quantum_circuit(data, params)
                readout = r0 + r1 * torch.sum(readout) / len(readout)
                readout = readout.view(-1)
                print("Output shape:", readout.shape)
                loss = loss_func(readout, target)
                batch_loss += loss
            batch_loss.backward()
            optimizer.step()
            total_train_loss += batch_loss.item()
        # Calculate average training loss for the epoch
        epoch_train_loss = total_train_loss / len(train_batches)
        train_losses.append(epoch_train_loss)
        print(f"Epoch {epoch+1}: Train Loss: {epoch_train_loss}")
        
        if (epoch + 1) % 5 == 0:
            total_val_loss = 0
            with torch.no_grad():
                val_batches = list(batch_processing(val_data, val_targets, batch_size))
                for batch_data, batch_targets in val_batches:
                    batch_loss = 0
                    for data, target in zip(batch_data, batch_targets):
                        readout = quantum_circuit(data, params)
                        readout = r0 + r1 * torch.sum(readout) / len(readout)
                        readout = readout.view(-1)
                        loss = loss_func(readout, target)
                        batch_loss += loss
                    total_val_loss += batch_loss.item()
        
            # Calculate average validation loss for this point
            epoch_val_loss = total_val_loss / len(val_batches)
            val_losses.append(epoch_val_loss)
            print(f"Validation Loss after Epoch {epoch+1}: {epoch_val_loss}")

    plt.figure(figsize=(10, 5))
    plt.plot(train_losses, label='Training Loss')
    plt.plot(val_losses, label='Validation Loss')
    plt.xlabel('Epochs')
    plt.ylabel('Loss')
    plt.title('Training and Validation Loss Curve')
    plt.legend()
    plt.grid(True)
    plt.show()


graph_data, targets = smiles_to_graph_and_targets(dataset_smiles, dataset)


filtered_graphs, filtered_targets = filter_graphs_by_num_atoms(graph_data, targets, num_atoms=6)


assert len(filtered_graphs) >= 600, "Not enough samples with 6 atoms"


selected_graphs = filtered_graphs[:600]
selected_targets = filtered_targets[:600]


(train_data, train_targets), (val_data, val_targets) = split_data(selected_graphs, selected_targets, 300, 300)


train_and_plot(train_data, train_targets, val_data, val_targets, batch_size=30)


Total graphs: 600, Total targets: 600
Input shape: torch.Size([6, 4])
Applying EDU on wires: [0, 1]
Applying EDU on wires: [2, 3]
Applying EDU on wires: [3, 4]
Applying EDU on wires: [4, 5]
Applying EDU on wires: [5, 2]
Applying EDU on wires: [1, 2]
Applying EDU on wires: [0, 1]
Applying EDU on wires: [2, 3]
Applying EDU on wires: [3, 4]
Applying EDU on wires: [4, 5]
Applying EDU on wires: [5, 2]
Applying EDU on wires: [1, 2]
Applying EDU on wires: [0, 1]
Applying EDU on wires: [2, 3]
Applying EDU on wires: [3, 4]
Applying EDU on wires: [4, 5]
Applying EDU on wires: [5, 2]
Applying EDU on wires: [1, 2]
Output shape: torch.Size([1])
Input shape: torch.Size([6, 4])
Applying EDU on wires: [1, 2]
Applying EDU on wires: [2, 3]
Applying EDU on wires: [2, 4]
Applying EDU on wires: [4, 5]
Applying EDU on wires: [0, 1]
Applying EDU on wires: [1, 2]
Applying EDU on wires: [2, 3]
Applying EDU on wires: [2, 4]
Applying EDU on wires: [4, 5]
Applying EDU on wires: [0, 1]
Applying EDU on wires: [1, 2

Plotting the circuit

In [21]:
def default_EDU(bond_params, rzz_param, wires):
    if len(wires) < 2:
        raise ValueError(f"Expected 'wires' to contain at least 2 elements, but got {len(wires)} elements: {wires}")
    
    print(f"Applying EDU on wires: {wires}")
    
    qml.RZ(bond_params[0], wires=wires[0])
    qml.RX(bond_params[1], wires=wires[0])
    qml.RZ(bond_params[0], wires=wires[1])
    qml.RX(bond_params[1], wires=wires[1])
    qml.CNOT(wires=wires)
    qml.RZ(rzz_param, wires=wires[1])
    qml.CNOT(wires=wires)
    qml.RX(bond_params[0], wires=wires[0])
    qml.RZ(bond_params[1], wires=wires[0])
    qml.RX(bond_params[0], wires=wires[1])
    qml.RZ(bond_params[1], wires=wires[1])
    

def quantum_circuit(graph, layer_params):
    num_layers = 3  # Fixed number of layers
    num_atoms = graph.num_nodes
    dev = qml.device('default.qubit', wires=num_atoms)

    @qml.qnode(dev)
    def circuit():
        encoded_features = quantum_encode(graph.x)
        for i in range(num_atoms):
            qml.RY(encoded_features[i][0], wires=i)
            qml.RZ(encoded_features[i][1], wires=i)

        for layer in range(num_layers):
            rzz_param = layer_params['rzz_params'][layer]
            for i in range(num_atoms):
                qml.U3(layer_params['theta'][layer], layer_params['phi'][layer], layer_params['omega'][layer], wires=i)
            bond_order = ['single', 'aromatic', 'double', 'triple']
            sorted_bonds = sorted(graph.bond_info, key=lambda x: bond_order.index(x[2]))
            for start, end, bond_type in sorted_bonds:
                bond_edu_params = layer_params['edu'][bond_type]
                default_EDU(bond_edu_params, rzz_param, [start, end])
        return [qml.expval(qml.PauliZ(i)) for i in range(num_atoms)]

    return circuit

def quantum_circuit(graph, layer_params):
    num_layers = 3  # Fixed number of layers
    num_atoms = graph.num_nodes
    dev = qml.device('default.qubit', wires=num_atoms)

    @qml.qnode(dev)
    def circuit():
        encoded_features = quantum_encode(graph.x)
        for i in range(num_atoms):
            qml.RY(encoded_features[i][0], wires=i)
            qml.RZ(encoded_features[i][1], wires=i)

        for layer in range(num_layers):  # Use the fixed number of layers
            rzz_param = layer_params['rzz_params'][layer]
            for i in range(num_atoms):
                qml.U3(layer_params['theta'][layer], layer_params['phi'][layer], layer_params['omega'][layer], wires=i)
            bond_order = ['single', 'aromatic', 'double', 'triple']
            sorted_bonds = sorted(graph.bond_info, key=lambda x: bond_order.index(x[2]))
            for start, end, bond_type in sorted_bonds:
                bond_edu_params = layer_params['edu'][bond_type]
                default_EDU(bond_edu_params, rzz_param, [start, end])
        return [qml.expval(qml.PauliZ(i)) for i in range(num_atoms)]

    return circuit

# Example data preparation steps
# Assuming dataset_smiles and dataset are already loaded
graph_data, targets = smiles_to_graph_and_targets(dataset_smiles, dataset)
(train_data, train_targets), (val_data, val_targets), (test_data, test_targets) = split_data(graph_data, targets, 10000, 1000, 1000)

# Set layer_params for visualization
layers = 3
num_atoms = max(len(data.x) for data in train_data)
layer_params = {
    'theta': [torch.tensor(np.random.random(num_atoms), dtype=torch.float32, requires_grad=True) for _ in range(layers)],
    'phi': [torch.tensor(np.random.random(num_atoms), dtype=torch.float32, requires_grad=True) for _ in range(layers)],
    'omega': [torch.tensor(np.random.random(num_atoms), dtype=torch.float32, requires_grad=True) for _ in range(layers)],
    'rzz_params': [torch.tensor(np.random.random(1), dtype=torch.float32, requires_grad=True) for _ in range(layers)],
    'edu': {
        'single': torch.tensor(np.random.random(2), dtype=torch.float32, requires_grad=True),
        'aromatic': torch.tensor(np.random.random(2), dtype=torch.float32, requires_grad=True),
        'double': torch.tensor(np.random.random(2), dtype=torch.float32, requires_grad=True),
        'triple': torch.tensor(np.random.random(2), dtype=torch.float32, requires_grad=True)
    }
}

# Generate the circuit for the first training sample and draw the diagram
circuit = quantum_circuit(train_data[0], layer_params)
drawer = qml.draw(circuit)
print(drawer())

Total graphs: 133885, Total targets: 133885
Applying EDU on wires: [0, 1]
Applying EDU on wires: [1, 2]
Applying EDU on wires: [1, 3]
Applying EDU on wires: [3, 4]
Applying EDU on wires: [4, 5]
Applying EDU on wires: [5, 6]
Applying EDU on wires: [6, 7]
Applying EDU on wires: [7, 8]
Applying EDU on wires: [8, 1]
Applying EDU on wires: [8, 4]
Applying EDU on wires: [7, 5]
Applying EDU on wires: [0, 1]
Applying EDU on wires: [1, 2]
Applying EDU on wires: [1, 3]
Applying EDU on wires: [3, 4]
Applying EDU on wires: [4, 5]
Applying EDU on wires: [5, 6]
Applying EDU on wires: [6, 7]
Applying EDU on wires: [7, 8]
Applying EDU on wires: [8, 1]
Applying EDU on wires: [8, 4]
Applying EDU on wires: [7, 5]
Applying EDU on wires: [0, 1]
Applying EDU on wires: [1, 2]
Applying EDU on wires: [1, 3]
Applying EDU on wires: [3, 4]
Applying EDU on wires: [4, 5]
Applying EDU on wires: [5, 6]
Applying EDU on wires: [6, 7]
Applying EDU on wires: [7, 8]
Applying EDU on wires: [8, 1]
Applying EDU on wires: [8,

Angle Extraction Network

In [ ]:
import torch
import torch.nn as nn

class AngleExtractionNetwork(nn.Module):
    def __init__(self, input_features, output_features):
        super().__init__()
        self.layer = nn.Sequential(
            nn.Linear(input_features, 128),
            nn.ReLU(),
            nn.Linear(128, output_features)
        )
    
    def forward(self, x):
        return self.layer(x)


In [ ]:
import pennylane as qml

def setup_quantum_circuit(num_qubits):
    dev = qml.device('default.qubit', wires=num_qubits)

    @qml.qnode(dev)
    def quantum_circuit(angle_params,edge_features, edge_indices):
        for i in range(num_qubits):
            qml.RY(angle_params[i, 0], wires=i)
            qml.RZ(angle_params[i, 1], wires=i)
            
        
        for layer in range(layers):
            if edge_indices.shape[1] > 0:
                for k in range(edge_indices.shape[1]):
                    start, end = edge_indices[0, k], edge_indices[1, k]
                    bond_type = edge_features[k]
                    if bond_type[0] == 1:
                        qml.CNOT(wires=[start, end])
                        qml.RY(angle_params[start][0], wires=end)
                    elif bond_type[1] == 1:
                        qml.CNOT(wires=[start, end])
                        qml.RZ(angle_params[start][1], wires=end)
                    if len(angle_params[start]) > 2 and bond_type[2] == 1:
                        qml.CNOT(wires=[start, end])
                        qml.RX(angle_params[start][2] * layer, wires=end)
                    if len(angle_params[start]) > 3 and bond_type[3] == 1:
                        qml.CNOT(wires=[start, end])
                        qml.Rot(angle_params[start][3] * layer, angle_params[start][3] * layer, angle_params[start][3] * layer, wires=end)

        return [qml.expval(qml.PauliZ(wires=i)) for i in range(num_qubits)]
    

    return quantum_circuit


In [ ]:
def integrate_classical_quantum(graph_data, angle_extractor):
    for i, graph in enumerate(graph_data[:10]):  
        features_np = graph.x.numpy()  
        features_torch = torch.from_numpy(features_np).float()
        
        # Get angles from the neural network
        angles = angle_extractor(features_torch)
        
        
        angles = angles.detach().numpy()
        
        
        quantum_circuit = setup_quantum_circuit(graph.num_nodes)
        edge_features_np = graph.edge_attr.numpy()
        edge_indices_np = graph.edge_index.numpy().T
        if edge_indices_np.size == 0:
            expectations = [0] * num_qubits
        else:
            expectations = quantum_circuit(encoded_params, edge_features_np, edge_indices_np)
    
        
        
        print(f"Quantum circuit output for graph {i+1}: {expectations}")


angle_extractor = AngleExtractionNetwork(input_features=4, output_features=2)
integrate_classical_quantum(graph_data, angle_extractor)
